The scripts should be run in order.
<br> Currently you are on 
<br>&emsp;&emsp;resume.ipynb
<br>&emsp;&emsp;job_selection.ipynb
<br>&ensp;->&nbsp;job_vectorise.ipynb

In [1]:
from glob import glob
from bs4 import BeautifulSoup
import logging, importlib, sys, string
import spacy
import pickle, os
import pandas as pd
import numpy as np
from spacy.lang.en import English
from spacy.lang.en.stop_words import STOP_WORDS
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
from sklearn.decomposition import TruncatedSVD
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
import matplotlib.pyplot as plt
from wordcloud import WordCloud
from mlxtend.frequent_patterns import fpgrowth
from _pckle import save_pickle_object, load_pickle_object
from _logging import set_logging
from _graph import show_word_cloud, show_word_cloud_frequencies
from _utility import gl

set_logging(logging)
df_jobs = load_pickle_object(gl.pkl_df_selected_jobs)
number_of_jobs = len(df_jobs)
logging.info(f"Number of job descriptions read is {number_of_jobs}")
nlp = English()

2022-12-30 14:10:13,519 | INFO : Loading pickle file from: pickle\pkl_df_selected_jobs.pkl


c:\Users\hijik\Anaconda3\lib\site-packages\seaborn\rcmod.py:82: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if LooseVersion(mpl.__version__) >= "3.0":
c:\Users\hijik\Anaconda3\lib\site-packages\setuptools\_distutils\version.py:346: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  other = LooseVersion(other)


2022-12-30 14:10:14,611 | INFO : Number of job descriptions read is 1204


In [2]:
def get_resume(file):
    clean_resume = lambda x: x.replace("\n", " ")
    
    file_path = os.path.join("Files\\UserInput", file)
    f = open(file_path, "r")
    resume_text = f.read()
    return clean_resume(resume_text)


In [3]:
def tokenise_words(text, nlp):
    word_tokens = nlp(text)
    # converts the words in word_tokens to lower case and then checks whether
    # they are present in stop_words or not
    tokens = [w for w in word_tokens if not w.is_stop and not w.is_punct and not w.is_space]
    return tokens

In [5]:
# Generate list of tokens for word clouds
list_body_tokens = []
list_bullet_point_tokens = []
list_title_tokens = []

# create 3 new columns for word tokens
df_jobs[gl.title_tokens] = ""
df_jobs[gl.body_tokens] = ""
df_jobs[gl.bullet_point_tokens] = ""

# Get word tokens for title, body, bullet points through the jobs dataframe
for i, row in df_jobs.iterrows():
    id = row[gl.id]
    body = row[gl.body]
    body_tokens = tokenise_words(body, nlp)
    df_jobs.at[id, gl.body_tokens] = body_tokens
    bullet_points = row[gl.bullet_points]
    bullet_point_tokens = tokenise_words(bullet_points, nlp)
    df_jobs.at[id, gl.bullet_point_tokens] = bullet_point_tokens
    titles = str(row[gl.title])
    title_tokens = tokenise_words(titles, nlp)
    df_jobs.at[id, gl.title_tokens] = title_tokens
    list_body_tokens.extend(body_tokens)
    list_bullet_point_tokens.extend(bullet_point_tokens)
    list_title_tokens.extend(title_tokens)


In [6]:
def tokens_to_text(list_tokens):
    text = ""
    for token in list_tokens:
        text += token.text + " "
    return text

In [7]:
text = tokens_to_text(list_title_tokens)
title = "word cloud for job titles"
show_word_cloud(text, title)

c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=transposed_font)
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:519: DeprecationWarning: ROTATE_90 is deprecated and will be removed in Pillow 10 (2023-07-01). Use Transpose.ROTATE_90 instead.
  orientation = (Image.ROTATE_90 if orientation is None else
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=transposed_font)
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=trans

2022-12-30 14:10:20,913 | INFO : Saved image: Images\wordcloud_word cloud for job titles.png


In [8]:
text = tokens_to_text(list_body_tokens)
title = "word cloud for job descriptions"
show_word_cloud(text, title)

c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=transposed_font)
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:519: DeprecationWarning: ROTATE_90 is deprecated and will be removed in Pillow 10 (2023-07-01). Use Transpose.ROTATE_90 instead.
  orientation = (Image.ROTATE_90 if orientation is None else
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=transposed_font)
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=trans

2022-12-30 14:10:24,600 | INFO : Saved image: Images\wordcloud_word cloud for job descriptions.png


In [9]:
text = tokens_to_text(list_bullet_point_tokens)
title = "word cloud for bullet points"
show_word_cloud(text, title)

c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=transposed_font)
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:519: DeprecationWarning: ROTATE_90 is deprecated and will be removed in Pillow 10 (2023-07-01). Use Transpose.ROTATE_90 instead.
  orientation = (Image.ROTATE_90 if orientation is None else
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=transposed_font)
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=trans

2022-12-30 14:10:26,164 | INFO : Saved image: Images\wordcloud_word cloud for bullet points.png


Check the important words using TD/IDF

In [10]:
# Remove tokens, no longer need them
drop_columns = [gl.title_tokens, gl.body_tokens, gl.bullet_point_tokens]
df_jobs.drop(columns=drop_columns, inplace=True)

In [11]:
def kmeans_wordclouds(tfIdf_svd, tfIdf_matrix, tag, k, word_positions):
    # Clustering
    in_model = KMeans(n_clusters=k, random_state=42)
    in_y_pred = in_model.fit_predict(tfIdf_svd)
    in_cluster_ids = set(in_y_pred)
    # silhouette score is used to evaluate the quality of the clusters
    silhouette_avg = silhouette_score(tfIdf_svd, in_y_pred)
    print(f"For n_clusters = {k} the average silhouette_score is :{silhouette_avg}")
    print("The closer the score is to 1 the better")
    
# Number of words with highest tfidf score to display
    top_count = 100
    for in_cluster_id in in_cluster_ids:
        # compute the total tfidf for each term in the cluster
        in_tfidf = tfIdf_matrix[in_y_pred == in_cluster_id]
        # numpy.matrix
        tfidf_sum = np.sum(in_tfidf, axis=0)
        # numpy.array of shape (1, X.shape[1])
        tfidf_sum = np.asarray(tfidf_sum).reshape(-1)
        top_indices = tfidf_sum.argsort()[-top_count:]
        term_weights = {word_positions[in_idx]: tfidf_sum[in_idx] for in_idx in top_indices}
        show_word_cloud_frequencies(term_weights, k, in_cluster_id, tag)

    return in_cluster_ids

In [12]:
def add_cosine_dataframe_column(df, tag, matrix_cosine_similarity):
    cosine_similarity = matrix_cosine_similarity.toarray()
    column_name = f"{tag}_Cosine_Similarity"
    df[column_name] = 0.0
    for j, (id, row) in enumerate(df.iterrows()):
        if j < len(cosine_similarity):
            df.at[id, column_name] = cosine_similarity[j]
    return df

In [13]:
def find_important_words(df, tag, tfIdfVectorizer):
    # Get the Bag of Words (BoW) matrix
    tfIdf_matrix = tfIdfVectorizer.fit_transform(df[tag])
    matrix_cosine_similarity = tfIdf_matrix[:-1] @ tfIdf_matrix[-1].T
    df = add_cosine_dataframe_column(df, tag, matrix_cosine_similarity)
 
    logging.info(df.tail())
    # Reduce the dimensionality of the sparse matrix by doing the PCA
    low_number_of_features = 30
    svd = TruncatedSVD(n_components=low_number_of_features, random_state=42)
    tfIdf_svd = svd.fit_transform(tfIdf_matrix)
    total_variance_explained = np.sum(svd.explained_variance_ratio_)
    logging.info(f"{tag}: Total variance explained: {total_variance_explained:.2f}")

    return df, tfIdf_svd, tfIdf_matrix, svd

In [14]:
def add_resume_to_jobs_dataframe(df_jobs):
    resume_id = df_jobs[gl.id].max() + 1
    resume_title = "resume"
    resume_text = get_resume(gl.txt_resume)
    resume_score = 1
    df_jobs.loc[len(df_jobs.index)] = [resume_id, resume_title, resume_text, resume_text, resume_score]
    return df_jobs

In [15]:
df_jobs = add_resume_to_jobs_dataframe(df_jobs)

tfIdfVectorizer=TfidfVectorizer(use_idf=True, 
                                lowercase=True,
                                max_df=0.8,
                                min_df=2,
                                #ngram_range=(1,3),
                                stop_words="english", 
                                )
list_tag = [gl.body, gl.bullet_points]
list_tfIdf = []
for tag in list_tag:
    df, tfIdf_svd, tfIdf_matrix, svd = find_important_words(df_jobs, tag, tfIdfVectorizer)
    word_positions = {v: k for k, v in tfIdfVectorizer.vocabulary_.items()}
    list_tfIdf.append((tfIdf_svd, tfIdf_matrix, word_positions))
    list_cluster_ids = []
    for i in range(2,6):
        cluster_ids = kmeans_wordclouds(tfIdf_svd, tfIdf_matrix, tag, i, word_positions)
        list_cluster_ids.append(cluster_ids)

2022-12-30 14:10:26,957 | INFO :         Id                                              Title  \
1454  1454              Data Analyst (Part-Time) - Austin, TX   
1455  1455  Manager - Business Development (Central and Ea...   
1456  1456  Natural Language Processing Undergraduate Inte...   
1457  1457     Political Staffer - San Francisco Bay Area, CA   
1204  1458                                             resume   

                                                   Body  \
1454  Data Analyst (Part-Time) - Austin, TX \nABOUT ...   
1455  Manager - Business Development (Central and Ea...   
1456  Natural Language Processing Undergraduate Inte...   
1457  Political Staffer - San Francisco Bay Area, CA...   
1204  Experience  1. Developed probability simulatio...   

                                          Bullet_Points     Score  \
1454   Performing ad-hoc statistical analysis (linea...  0.796964   
1455   Drive New Sales from prospective clients with...  0.792253   
1456   Design 

c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=transposed_font)
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:519: DeprecationWarning: ROTATE_90 is deprecated and will be removed in Pillow 10 (2023-07-01). Use Transpose.ROTATE_90 instead.
  orientation = (Image.ROTATE_90 if orientation is None else
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=transposed_font)
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=trans

2022-12-30 14:10:28,715 | INFO : Saved image: Images\wordcloud_Body_kmeans_2_cluster_0.png


c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=transposed_font)
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:519: DeprecationWarning: ROTATE_90 is deprecated and will be removed in Pillow 10 (2023-07-01). Use Transpose.ROTATE_90 instead.
  orientation = (Image.ROTATE_90 if orientation is None else
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=transposed_font)
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=trans

2022-12-30 14:10:30,065 | INFO : Saved image: Images\wordcloud_Body_kmeans_2_cluster_1.png
For n_clusters = 3 the average silhouette_score is :0.06731528223811868
The closer the score is to 1 the better


...

2022-12-30 14:11:06,065 | INFO : Saved image: Images\wordcloud_Bullet_Points_kmeans_5_cluster_2.png


c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:499: DeprecationWarning: ROTATE_90 is deprecated and will be removed in Pillow 10 (2023-07-01). Use Transpose.ROTATE_90 instead.
  orientation = Image.ROTATE_90
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=transposed_font)
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:520: DeprecationWarning: ROTATE_90 is deprecated and will be removed in Pillow 10 (2023-07-01). Use Transpose.ROTATE_90 instead.
  Image.ROTATE_90)
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=transposed_font)
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wo

2022-12-30 14:11:07,951 | INFO : Saved image: Images\wordcloud_Bullet_Points_kmeans_5_cluster_3.png


c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=transposed_font)
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:519: DeprecationWarning: ROTATE_90 is deprecated and will be removed in Pillow 10 (2023-07-01). Use Transpose.ROTATE_90 instead.
  orientation = (Image.ROTATE_90 if orientation is None else
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=transposed_font)
c:\Users\hijik\Anaconda3\lib\site-packages\wordcloud\wordcloud.py:508: DeprecationWarning: textsize is deprecated and will be removed in Pillow 10 (2023-07-01). Use textbbox or textlength instead.
  box_size = draw.textsize(word, font=trans

2022-12-30 14:11:09,474 | INFO : Saved image: Images\wordcloud_Bullet_Points_kmeans_5_cluster_4.png


In [16]:
def k_means(svd, word_positions, X_tfidf, n_clusters = 4):
    n_jobs=-1
    model = KMeans(n_clusters=n_clusters, random_state=42)
    y_pred = model.fit_predict(svd)
    cluster_ids = set(y_pred)
    min_support = 0.3
    dist_words = sorted(v for k, v in word_positions.items()) # distinct words in the vocabulary
    for cluster_id in cluster_ids:
        print(f"FP-Growth results on Cluster {cluster_id} with min support {min_support}")
        tfidf = X_tfidf[y_pred == cluster_id]
        # encoded as binary "presence/absence" representation as required by mlxtend
        tfidf[tfidf > 0] = 1
        # df is a pandas sparse dataframe
        df = pd.DataFrame.sparse.from_spmatrix(tfidf, columns=dist_words)
        fset = fpgrowth(df, min_support=min_support, use_colnames=True).sort_values(by='support', ascending=False)
        print(fset, '\n')


In [17]:
n_clusters = 4
for (tfidf, svd, word_positions) in list_tfIdf:
    k_means(svd, word_positions, tfidf, n_clusters)

FP-Growth results on Cluster 0 with min support 0.3


AttributeError: 'numpy.ndarray' object has no attribute 'tocsc'

In [ ]:
df_body = list_tfIdf[0]
print(f"Most important words in job description\n{df_body.head(20)}")


IndexError: list index out of range

In [ ]:
df_bullet_points = list_tfIdf[1]
print(f"Most important words in bullet points\n{df_bullet_points.head(20)}")

IndexError: list index out of range